# Debug Runt Transform
template for testing/debugging runt transforms

In [11]:
import sys
import os
from os import sep
from os.path import dirname, realpath
from pathlib import Path
import logging
logging.basicConfig(stream=sys.stdout, level=logging.DEBUG)

def get_cwd(fname, subdir, crunch_dir=realpath(Path.home()) +sep +'crunch' +sep):
    """
    Convenience function to make a directory string for the current file based on inputs.
    Jupyter Notebook in Anaconda invokes the Python interpreter in Anaconda's subdirectory
    which is why changing sys.argv[0] is necessary. In the future a better way to do this
    should be preferred..
    """
    return crunch_dir +subdir +fname
    
def fix_path(cwd):
    """
    Convenience function to fix argv and python path so that jupyter notebook can run the same as
    any script in crunch.
    """
    sys.argv[0] = cwd
    module_path = os.path.abspath(os.path.join('..'))
    if module_path not in sys.path:
        sys.path.append(module_path)

fix_path(get_cwd('test.ipynb', 'recon' +sep))

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from numba import jit, vectorize
from dask import delayed, dataframe as dd

from ipywidgets import interact, interactive, fixed
from IPython.display import display

pd.set_option("display.max_rows", 100)
pd.set_option('display.max_columns', 50)

from common_util import MUTATE_DIR, DT_HOURLY_FREQ, DT_CAL_DAILY_FREQ
from common_util import load_json, dump_json, remove_dups_list, list_get_dict, is_empty_df, search_df, benchmark
from data.data_api import DataAPI
from data.access_util import df_getters as dg, col_subsetters2 as cs2
from mutate.common import default_runt_dir_name, default_trfs_dir_name
from mutate.runt_util import *
from mutate.runt import fill_defaults, get_variants, get_row_mask_keychain, get_desc_pfx, make_runt_entry

## General

### Set Logging Level and Date Range

In [2]:
logging.basicConfig(stream=sys.stdout, level=logging.DEBUG)
date_range = {
    'id': ('lt', 2018)
}

### Set Runt and Transform Directories

In [3]:
runt_dir_name = default_runt_dir_name
trfs_dir_name = default_trfs_dir_name

runt_dir = MUTATE_DIR +runt_dir_name
trfs_dir = runt_dir +trfs_dir_name

### Load all transforms

In [4]:
trf_defaults = load_json('trf_defaults.json', dir_path=runt_dir)
graph = load_json('graph.json', dir_path=runt_dir)
trfs = {}

logging.info('loading step settings...')
for fname in os.listdir(trfs_dir):
    trf = load_json(fname, dir_path=trfs_dir)
    trfs[trf['meta']['name']] = trf

INFO:root:loading step settings...


### Define Test Step Function

In [1]:
def test_step(step_info, date_range, overwrites = {}):
    meta, fn, var, rm, src, dst = step_info['meta'], step_info['fn'], step_info['var'], step_info['rm'], step_info['src'], step_info['dst']

    # Loading transform, apply, and frequency settings
    ser_fn = overwrites['ser_fn'] if ('ser_fn' in overwrites) else RUNT_FN_TRANSLATOR[fn['ser_fn']]
    rtype_fn = overwrites['df_fn'] if ('df_fn' in overwrites) else RUNT_TYPE_TRANSLATOR[fn['df_fn']]
    col_fn = overwrites['col_fn'] if ('col_fn' in overwrites) else RUNT_NMAP_TRANSLATOR[fn['col_fn']]
    freq = overwrites['freq'] if ('freq' in overwrites) else RUNT_FREQ_TRANSLATOR[fn['freq']]
    res_freq = RUNT_FREQ_TRANSLATOR[meta['res_freq']]

    # Making all possible parameter combinations
    variants = get_variants(var, meta['var_fmt'])

    # Loading row mask, if any
    if (rm is not None):
        rm_dg, rm_cs = list_get_dict(dg, rm), list_get_dict(cs2, rm)
        rm_paths, rm_recs, rm_dfs = DataAPI.load_from_dg(rm_dg, rm_cs)
        rm_keys = [remove_dups_list([key_chain[i] for key_chain in rm_paths]) for i in range(len(rm_paths[0]))]

    # Loading input data
    src_dg, src_cs = list_get_dict(dg, src), list_get_dict(cs2, src)
    src_paths, src_recs, src_dfs = DataAPI.load_from_dg(src_dg, src_cs)
    logging.debug('src_paths[0] ' +str(src_paths[0]))
    logging.debug('src_paths[-1] ' +str(src_paths[-1]))

    # Run transforms on inputs
    for key_chain in src_paths:
        logging.info('data: ' +str('_'.join(key_chain)))
        src_rec, src_df = list_get_dict(src_recs, key_chain), list_get_dict(src_dfs, key_chain)
        src_df = src_df.loc[search_df(src_df, date_range), :].dropna(axis=0, how='all')

        # Masking rows in src from row mask
        if (rm is not None):
            rm_key_chain = get_row_mask_keychain(key_chain, rm_keys)
            rm_df = list_get_dict(rm_dfs, rm_key_chain).dropna()
            not_in_src = rm_df.index.difference(src_df.index)
            logging.debug('row mask: ' +str('_'.join(rm_key_chain)))
            if (len(not_in_src)>0):
                logging.debug('rm_idx - src_idx: ' +str(not_in_src))
                src_df = src_df.loc[src_df.index & rm_df.index, :].dropna(axis=0, how='all')
            else:
                src_df = src_df.loc[rm_df.index, :].dropna(axis=0, how='all')

        logging.debug('pre_transform: ' +str(src_df))

        # Running variants of the transform
        for variant in variants:
            runted_df = rtype_fn(src_df, ser_fn(**variant), freq, col_fn())
            desc_sfx = meta['rec_fmt'].format(**variant)
            desc_pfx = get_desc_pfx(key_chain, src_rec)
            desc = '_'.join([desc_pfx, desc_sfx])

            if (meta['mtype_from']=='name'):       mutate_type = meta['name']
            elif (meta['mtype_from']=='rec_fmt'):  mutate_type = desc_sfx

            assert(not is_empty_df(runted_df))
            entry = make_runt_entry(desc, res_freq, mutate_type, src_rec)
            logging.info('dumping ' +desc +'...')
            logging.debug('post_transform: ' +str(runted_df))
            yield entry, runted_df

## Transform Debug

### Set Transform
Fill it in (default is day moving average)

In [6]:
trf_name = 'dma'

### Imports

In [7]:
from mutate.fracdiff import *

### Test Section

In [8]:
logging.basicConfig(stream=sys.stdout, level=logging.INFO)

In [9]:
trf = trfs[trf_name]
step = fill_defaults(trf, trf_defaults)

In [12]:
for runt_rec, runt_df in test_step(step, date_range):
    print(runt_df)

DEBUG:root:src_paths[0] ['dow_jones', 'drf', 'raw_pba']
DEBUG:root:src_paths[-1] ['russell_2000', 'drl', 'thresh_vol']
INFO:root:data: dow_jones_drf_raw_pba
DEBUG:root:pre_transform:                            pba_open  pba_close  pba_avgPrice  pba_numTrades
id                                                                         
1998-01-02 00:00:00+00:00   7910.24    7923.19     7933.6658          179.0
1998-01-05 00:00:00+00:00   7967.04    7963.80     7970.0015          179.0
1998-01-06 00:00:00+00:00   7978.25    7933.41     7925.0406          179.0
1998-01-07 00:00:00+00:00   7904.76    7880.10     7880.6830          178.0
1998-01-08 00:00:00+00:00   7902.02    7844.97     7856.5759          179.0
1998-01-09 00:00:00+00:00   7799.88    7732.87     7754.3262          179.0
1998-01-12 00:00:00+00:00   7571.70    7534.33     7494.4991          179.0
1998-01-13 00:00:00+00:00   7646.93    7688.03     7686.9030          178.0
1998-01-14 00:00:00+00:00   7732.13    7731.13     7738.1

                               pba_open     pba_close  pba_avgPrice  \
id                                                                    
1998-01-06 00:00:00+00:00   7951.843333   7940.133333   7942.902633   
1998-01-07 00:00:00+00:00   7950.016667   7925.770000   7925.241700   
1998-01-08 00:00:00+00:00   7928.343333   7886.160000   7887.433167   
1998-01-09 00:00:00+00:00   7868.886667   7819.313333   7830.528367   
1998-01-12 00:00:00+00:00   7757.866667   7704.056667   7701.800400   
1998-01-13 00:00:00+00:00   7672.836667   7651.743333   7645.242767   
1998-01-14 00:00:00+00:00   7650.253333   7651.163333   7639.839667   
1998-01-15 00:00:00+00:00   7720.336667   7723.820000   7726.425333   
1998-01-16 00:00:00+00:00   7738.023333   7747.153333   7749.720467   
1998-01-20 00:00:00+00:00   7745.080000   7755.956667   7759.764933   
1998-01-21 00:00:00+00:00   7774.226667   7776.466667   7783.515200   
1998-01-22 00:00:00+00:00   7805.366667   7770.573333   7782.477333   
1998-0

DEBUG:root:post_transform:                             pba_open  pba_close  pba_avgPrice  pba_numTrades
id                                                                          
1998-01-08 00:00:00+00:00   7932.462   7909.094    7913.19336          178.8
1998-01-09 00:00:00+00:00   7910.390   7871.030    7877.32544          178.8
1998-01-12 00:00:00+00:00   7831.322   7785.136    7782.22496          178.8
1998-01-13 00:00:00+00:00   7765.058   7736.060    7734.59744          178.6
1998-01-14 00:00:00+00:00   7730.532   7706.266    7706.08422          178.8
1998-01-15 00:00:00+00:00   7706.518   7687.732    7685.62026          178.6
1998-01-16 00:00:00+00:00   7686.540   7692.764    7686.11270          178.6
1998-01-20 00:00:00+00:00   7722.860   7737.406    7740.86294          178.6
1998-01-21 00:00:00+00:00   7767.352   7762.566    7768.58372          178.8
1998-01-22 00:00:00+00:00   7779.608   7764.410    7771.69530          178.8
1998-01-23 00:00:00+00:00   7769.244   7766.454  

DEBUG:root:post_transform:                             pba_open  pba_close  pba_avgPrice  pba_numTrades
id                                                                          
1998-01-15 00:00:00+00:00   7819.490   7798.413    7799.40681          178.7
1998-01-16 00:00:00+00:00   7798.465   7781.897    7781.71907          178.7
1998-01-20 00:00:00+00:00   7777.091   7761.271    7761.54395          178.7
1998-01-21 00:00:00+00:00   7766.205   7749.313    7751.59058          178.7
1998-01-22 00:00:00+00:00   7755.070   7735.338    7738.88976          178.8
1998-01-23 00:00:00+00:00   7737.881   7727.093    7729.68938          178.8
1998-01-26 00:00:00+00:00   7728.066   7726.346    7726.98859          178.8
1998-01-27 00:00:00+00:00   7742.689   7748.019    7751.32328          178.7
1998-01-28 00:00:00+00:00   7759.504   7764.710    7767.67554          178.7
1998-01-29 00:00:00+00:00   7777.963   7783.568    7784.29378          178.5
1998-01-30 00:00:00+00:00   7796.870   7800.931  

INFO:root:dumping raw_pba_drf_dma(20)...
DEBUG:root:post_transform:                              pba_open   pba_close  pba_avgPrice  pba_numTrades
id                                                                            
1998-01-30 00:00:00+00:00   7808.1800   7799.6720   7801.820555         178.65
1998-02-02 00:00:00+00:00   7808.3170   7805.9745   7805.727600         178.60
1998-02-03 00:00:00+00:00   7815.2420   7811.5920   7811.195685         178.55
1998-02-04 00:00:00+00:00   7824.0975   7820.1610   7820.964260         178.55
1998-02-05 00:00:00+00:00   7835.2700   7834.4350   7835.193380         178.55
1998-02-06 00:00:00+00:00   7845.8570   7850.5400   7849.613415         178.55
1998-02-09 00:00:00+00:00   7865.4375   7874.4550   7871.731815         178.55
1998-02-10 00:00:00+00:00   7895.8785   7907.9105   7907.019025         178.55
1998-02-11 00:00:00+00:00   7928.0885   7938.4640   7937.232650         178.60
1998-02-12 00:00:00+00:00   7957.0350   7965.8410   7964.266005

...

INFO:root:dumping thresh_vol_drl_dma(5)...
DEBUG:root:post_transform:                            vol_oc_return_fth_of_xact  \
id                                                     
2005-03-24 00:00:00+00:00                   0.003762   
2005-03-28 00:00:00+00:00                   0.004348   
2005-03-29 00:00:00+00:00                   0.001242   
2005-03-30 00:00:00+00:00                  -0.000282   
2005-03-31 00:00:00+00:00                  -0.000270   
2005-04-01 00:00:00+00:00                   0.000456   
2005-04-04 00:00:00+00:00                  -0.002026   
2005-04-05 00:00:00+00:00                  -0.001918   
2005-04-06 00:00:00+00:00                  -0.005471   
2005-04-07 00:00:00+00:00                  -0.006288   
2005-04-08 00:00:00+00:00                  -0.004079   
2005-04-11 00:00:00+00:00                  -0.010556   
2005-04-12 00:00:00+00:00                  -0.008160   
2005-04-13 00:00:00+00:00                  -0.006744   
2005-04-14 00:00:00+00:00         

                           vol_oc_return_fth_of_xact  \
id                                                     
2005-03-24 00:00:00+00:00                   0.003762   
2005-03-28 00:00:00+00:00                   0.004348   
2005-03-29 00:00:00+00:00                   0.001242   
2005-03-30 00:00:00+00:00                  -0.000282   
2005-03-31 00:00:00+00:00                  -0.000270   
2005-04-01 00:00:00+00:00                   0.000456   
2005-04-04 00:00:00+00:00                  -0.002026   
2005-04-05 00:00:00+00:00                  -0.001918   
2005-04-06 00:00:00+00:00                  -0.005471   
2005-04-07 00:00:00+00:00                  -0.006288   
2005-04-08 00:00:00+00:00                  -0.004079   
2005-04-11 00:00:00+00:00                  -0.010556   
2005-04-12 00:00:00+00:00                  -0.008160   
2005-04-13 00:00:00+00:00                  -0.006744   
2005-04-14 00:00:00+00:00                  -0.004681   
2005-04-15 00:00:00+00:00                  -0.00

INFO:root:dumping thresh_vol_drl_dma(10)...
DEBUG:root:post_transform:                            vol_oc_return_fth_of_xact  \
id                                                     
2005-04-01 00:00:00+00:00                   0.002109   
2005-04-04 00:00:00+00:00                   0.001161   
2005-04-05 00:00:00+00:00                  -0.000338   
2005-04-06 00:00:00+00:00                  -0.002876   
2005-04-07 00:00:00+00:00                  -0.003279   
2005-04-08 00:00:00+00:00                  -0.001812   
2005-04-11 00:00:00+00:00                  -0.006291   
2005-04-12 00:00:00+00:00                  -0.005039   
2005-04-13 00:00:00+00:00                  -0.006107   
2005-04-14 00:00:00+00:00                  -0.005484   
2005-04-15 00:00:00+00:00                  -0.003293   
2005-04-18 00:00:00+00:00                  -0.003156   
2005-04-19 00:00:00+00:00                  -0.003612   
2005-04-20 00:00:00+00:00                  -0.002921   
2005-04-21 00:00:00+00:00        

                           vol_oc_return_fth_of_xact  \
id                                                     
2005-04-01 00:00:00+00:00                   0.002109   
2005-04-04 00:00:00+00:00                   0.001161   
2005-04-05 00:00:00+00:00                  -0.000338   
2005-04-06 00:00:00+00:00                  -0.002876   
2005-04-07 00:00:00+00:00                  -0.003279   
2005-04-08 00:00:00+00:00                  -0.001812   
2005-04-11 00:00:00+00:00                  -0.006291   
2005-04-12 00:00:00+00:00                  -0.005039   
2005-04-13 00:00:00+00:00                  -0.006107   
2005-04-14 00:00:00+00:00                  -0.005484   
2005-04-15 00:00:00+00:00                  -0.003293   
2005-04-18 00:00:00+00:00                  -0.003156   
2005-04-19 00:00:00+00:00                  -0.003612   
2005-04-20 00:00:00+00:00                  -0.002921   
2005-04-21 00:00:00+00:00                  -0.002525   
2005-04-22 00:00:00+00:00                  -0.00

KeyboardInterrupt: 